In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import os
import math
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import rc
%matplotlib inline
from matplotlib import font_manager
from tqdm import tqdm
import folium
from folium.plugins import MarkerCluster


from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, confusion_matrix,r2_score,mean_absolute_error,mean_squared_error
from sklearn import preprocessing
from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import GridSearchCV
import xgboost
import joblib


pd.set_option("display.max_columns", None)


### Load해서 대입해보기

In [2]:
scaler = joblib.load('s_scale_0608.pkl')
xgb_reg = joblib.load('xgb_reg_0608.pkl')
rand_reg = joblib.load('randforest_0608.pkl')
df = pd.read_csv('usedcar_total_0604.csv')
searh_car = pd.read_csv('search_vector.csv')

searh_car

use  mileage  year  change  nation_국산  nation_수입  car_brand_BMW  \
0  103   131493  2013       1          1          0              0   

   car_brand_GMC  car_brand_MAN  car_brand_기아  car_brand_닛산  car_brand_다이하쓰  \
0              0              0             0             0               0   

   car_brand_닷지  car_brand_도요타  car_brand_동풍자동차  car_brand_람보르기니  \
0             0              0                0                0   

   car_brand_랜드로버  car_brand_렉서스  car_brand_로버  car_brand_롤스로이스  \
0               0              0             0                0   

   car_brand_르노삼성  car_brand_르노코리아  car_brand_링컨  car_brand_마세라티  \
0               0                0             0               0   

   car_brand_마이바흐  car_brand_마쯔다  car_brand_맥라렌  car_brand_미니  car_brand_미쯔비시  \
0               0              0              0             0               0   

   car_brand_벤츠  car_brand_벤틀리  car_brand_볼보  car_brand_사브  car_brand_선롱버스  \
0             0              0             0             0               0   

   car_brand_쉐보레  car_brand_스마트  car_brand_스바루  car_brand_스즈키  car_brand_시트로엥  \
0              0              0              0              0               0   

   car_brand_쌍용  car_brand_아우디  car_brand_애스턴마틴  car_brand_어큐라  car_brand_이베코  \
0             0              0                0              0              0   

   car_brand_인피니티  car_brand_재규어  car_brand_제네시스  car_brand_중한자동차  \
0               0              0               0                0   

   car_brand_지프  car_brand_캐딜락  car_brand_크라이슬러  car_brand_테슬라  car_brand_페라리  \
0             0              0                0              0              0   

   car_brand_포드  car_brand_포르쉐  car_brand_포톤  car_brand_폭스바겐  car_brand_푸조  \
0             0              0             0               0             0   

   car_brand_피아트  car_brand_한국GM  car_brand_허머  car_brand_현대  car_brand_혼다  \
0              0               1             0             0             0   

   car_model_1시리즈  car_model_200  car_model_2008  car_model_206  \
0               0              0               0              0   

   car_model_207  car_model_208  car_model_2시리즈  car_model_3008  \
0              0              0               0               0   

   car_model_300C  car_model_307  car_model_308  car_model_370Z  \
0               0              0              0               0   

   car_model_3시리즈  car_model_406  car_model_407  car_model_488 스파이더  \
0               0              0              0                   0   

   car_model_4시리즈  car_model_500  car_model_508  car_model_57  car_model_570S  \
0               0              0              0             0               0   

   car_model_5시리즈  car_model_62s  car_model_650S  car_model_675LT  \
0               0              0               0                0   

   car_model_6시리즈  car_model_720S  car_model_7시리즈  car_model_86  \
0               0               0               0             0   

   car_model_8시리즈  car_model_9-3  car_model_9-5  car_model_911  car_model_A1  \
0               0              0              0              0             0   

   car_model_A3  car_model_A4  car_model_A5  car_model_A6  car_model_A7  \
0             0             0             0             0             0   

   car_model_A8  car_model_ALL NEW ESCALADE  car_model_AMG GT  car_model_ATS  \
0             0                           0                 0              0   

   car_model_ATS-V  car_model_A클래스  car_model_BH  car_model_BLS  car_model_BS  \
0                0               0             0              0             0   

   car_model_B클래스  car_model_B클래스 W246  car_model_C3  car_model_C4  \
0               0                    0             0             0   

   car_model_C5  car_model_C70  car_model_CC  car_model_CK 미니 밴  \
0             0              0             0                  0   

   car_model_CK 미니 트럭  car_model_CLA클래스  car_model_CLK클래스  car_model_CL클래스  \
0                   0                 0                 0

In [3]:
searh_car.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Columns: 624 entries, use to insurance_있음
dtypes: int64(624)
memory usage: 5.0 KB


In [4]:
new_car = int(input('신차가격을 숫자만 입력해주세요(단위 : 만원)(ex 7000) :')) # 최종감가상각률에 잔존가치 금액으로 반환하기 위함
use = int(input('사용개월 수를 숫자만 작성해주세요(ex 1년 >> 12) : ')) 
mileage = int(input('주행거리를 숫자만 입력해주세요(단위 : km)(ex 50000) : '))
year = int(input('차량의 연식을 4자리 형태의 숫자만 입력해주세요(ex 2018) : '))
change = int(input('소유주 변경횟수를 숫자만 입력해주세요(ex 3) : '))


nation  = (input(f'{df.nation.unique()} 에서 선택해주세요 : '))
car_brand = input(f"{df[df['nation'] == nation]['car_brand'].unique()} 에서 선택해주세요 : ")
car_model = input(f"{df[df['car_brand'] == car_brand]['car_model'].unique()} 에서 선택해주세요 : ")
car_type = input(f"{df[df['car_model'] == car_model]['car_type'].unique()} 에서 선택해주세요 : ")
fuel = input(f'{df.fuel.unique()} 에서 선택해주세요 : ')
trans = input(f'{df.trans.unique()} 에서 선택해주세요 : ')
loss = input(f'전손이력을 {df.loss.unique()} 에서 선택해주세요 : ')
flood = input(f'침수이력을 {df.flood.unique()} 에서 선택해주세요 : ')
usage = input(f'용도이력을 {df.usage.unique()} 에서 선택해주세요 : ')
insurance = input(f'보험사고정보를 {df.insurance.unique()} 에서 선택해주세요 : ')

신차가격을 숫자만 입력해주세요(단위 : 만원)(ex 7000) :2107
사용개월 수를 숫자만 작성해주세요(ex 1년 >> 12) : 80
주행거리를 숫자만 입력해주세요(단위 : km)(ex 50000) : 143967
차량의 연식을 4자리 형태의 숫자만 입력해주세요(ex 2018) : 2016
소유주 변경횟수를 숫자만 입력해주세요(ex 3) : 2
['국산' '수입'] 에서 선택해주세요 : 국산
['한국GM' '르노삼성' '르노코리아' '쌍용' '제네시스' '현대' '기아'] 에서 선택해주세요 : 기아
['카니발' '스포티지' '오피러스' 'K5' '모닝' 'K3' '레이' 'K7' '스팅어' '쏘렌토' '봉고' '쏘울' '카렌스'
 '프라이드' '모하비' '포르테' '니로' '마스터' '스토닉' '셀토스' 'K9' 'K8' '옵티마' '로체' '쎄라토'
 '라이노' '비스토' '프런티어' '스펙트라' '뉴그랜버드'] 에서 선택해주세요 : K5
['중형'] 에서 선택해주세요 : 중형
['LPG' '디젤' '가솔린' '하이브리드(가솔린)' 'CNG' '전기' '가솔린+LPG' '기타' '하이브리드(디젤)'
 '하이브리드(LPG)'] 에서 선택해주세요 : LPG
['오토' '수동' '기타' 'SAT' 'CVT'] 에서 선택해주세요 : 오토
전손이력을 ['없음' '있음'] 에서 선택해주세요 : 없음
침수이력을 ['없음' '있음'] 에서 선택해주세요 : 없음
용도이력을 ['없음' '있음'] 에서 선택해주세요 : 있음
보험사고정보를 ['있음' '없음'] 에서 선택해주세요 : 있음


In [5]:
for i,column in enumerate(searh_car.columns):
    if i <= 3 :
        searh_car[column] = 0
    else :
        searh_car[column] = np.uint8(0)

searh_car['use'] = use
searh_car['mileage'] = mileage
searh_car['year'] = year
searh_car['change'] = change

searh_car[f'nation_{nation}'] = np.uint8(1)
searh_car[f'car_brand_{car_brand}'] = np.uint8(1)
searh_car[f'car_model_{car_model}'] = np.uint8(1)
searh_car[f'car_type_{car_type}'] = np.uint8(1)
searh_car[f'fuel_{fuel}'] = np.uint8(1)
searh_car[f'trans_{trans}'] = np.uint8(1)
searh_car[f'loss_{loss}'] = np.uint8(1)
searh_car[f'flood_{flood}'] = np.uint8(1)
searh_car[f'usage_{usage}'] = np.uint8(1)
searh_car[f'insurance_{insurance}'] = np.uint8(1)

In [6]:
searh_car.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Columns: 624 entries, use to insurance_있음
dtypes: int64(4), uint8(620)
memory usage: 780.0 bytes


In [7]:
# change(사용자변경회수)
selected = 0
for col in searh_car.columns:
    if searh_car[col][0] != 0:
        selected += 1
        print(f'{col} : {searh_car[col][0]}')
print(selected)

use : 80
mileage : 143967
year : 2016
change : 2
nation_국산 : 1
car_brand_기아 : 1
car_model_K5 : 1
car_type_중형 : 1
fuel_LPG : 1
trans_오토 : 1
loss_없음 : 1
flood_없음 : 1
usage_있음 : 1
insurance_있음 : 1
14


In [8]:
scaled_searh_car= scaler.transform(searh_car)
scaled_searh_car

array([[-1.41542165e-01,  5.26460437e-01,  3.00649225e-01,
        -2.26827536e-01,  5.74532761e-01, -5.74532761e-01,
        -2.43206265e-01, -7.45832649e-03, -3.33539079e-03,
         1.63040758e+00, -5.72834749e-02, -8.17023277e-03,
        -1.52863815e-02, -5.09783599e-02, -1.15548397e-02,
        -6.67089290e-03, -1.08505509e-01, -7.42612042e-02,
        -6.67089290e-03, -1.20267253e-02, -2.27109474e-01,
        -1.06653718e-01, -5.44789410e-02, -5.50917830e-02,
        -4.71698113e-03, -4.71698113e-03, -7.45832649e-03,
        -1.12932635e-01, -1.24807921e-02, -2.46320925e-01,
        -2.77163223e-02, -7.02952237e-02, -1.10628552e-02,
        -6.67089290e-03, -2.75145932e-02, -1.10628552e-02,
        -1.15548397e-02, -8.82490909e-03, -2.88972287e-02,
        -2.58612265e-01, -1.62982907e-01, -1.15548397e-02,
        -4.71698113e-03, -3.33539079e-03, -6.01451920e-02,
        -7.94603747e-02, -1.83784841e-01, -1.52863815e-02,
        -8.44140454e-02, -4.55355480e-02, -4.57802185e-0

In [9]:
xgb_reg_predict = xgb_reg.predict(scaled_searh_car)
xgb_reg_predict = xgb_reg_predict[0].astype('float64')

#if xgb_reg_predict >= 15 :
#    xgb_reg_predict += 4.58
#else :
#    pass

rand_reg_predict = rand_reg.predict(scaled_searh_car)
rand_reg_predict = rand_reg_predict[0].astype('float64')

#if rand_reg_predict >= 15 :
#    rand_reg_predict += 4.78
#else :
#    pass

In [10]:
xgb_reg_dep = round(xgb_reg_predict.astype('float64'),1)
print(f'Model Depreciation Predict : {xgb_reg_dep}% 감가')
xgb_price = [math.trunc(new_car * (100 - (int(math.ceil(xgb_reg_predict))))/100), math.ceil(new_car * (100 - (int(math.trunc(xgb_reg_predict))))/100)]
print(f'XGBoost Usedcar Price Predict : {xgb_price[0]} ~ {xgb_price[1]} 만원입니다.')

rand_reg_dep = round(rand_reg_predict.astype('float64'),1)
print(f'Model Depreciation Predict : {rand_reg_dep}% 감가')
rand_price = [math.trunc(new_car * (100 - (int(math.ceil(rand_reg_predict))))/100), math.ceil(new_car * (100 - (int(math.trunc(rand_reg_predict))))/100)]
print(f'RandomForest Usedcar Price Predict : {rand_price[0]} ~ {rand_price[1]} 만원입니다.')


Model Depreciation Predict : 50.4% 감가
XGBoost Usedcar Price Predict : 1032 ~ 1054 만원입니다.
Model Depreciation Predict : 54.5% 감가
RandomForest Usedcar Price Predict : 948 ~ 970 만원입니다.


In [11]:
price_min = (xgb_price[0]+rand_price[0])/2
price_max = (xgb_price[1]+rand_price[1])/2

In [12]:
print(f'Usedcar Price Predict : {price_min} ~ {price_max} 만원입니다.')

Usedcar Price Predict : 990.0 ~ 1012.0 만원입니다.


# 실측값 비교해보기( 시각화 , 모델탑재, folium 먼저)

In [13]:
search_car_list = df[df['car_model']==car_model].index

In [26]:
def show_map(lat=36.24, lng=128):
    center = [lat,lng]
    m =folium.Map(location=center,
             zoom_start=7.3,
             width = 500,
             height = 400,
                 tiles = 'cartodbpositron')
    
    cluster = MarkerCluster().add_to(m)
    for car_idx in search_car_list:
        folium.Marker(location = [df['lat'][car_idx], df['lng'][car_idx]],
                     tooltip = df['sales_corp'][car_idx],
                     popup =f"<pre>{df['car_model'][car_idx]}{df['name_detailed'][car_idx]}</pre><pre>번호판: {df['car_no'][car_idx]} 가격: {df['price'][car_idx]}만원</pre>",
                     icon = folium.Icon(icon='Car', color ='red')).add_to(cluster)
    
    return m

In [27]:
m = show_map()

In [28]:
m

In [ ]:
m.save(f'{car_model}.html')